In [2]:
import random
import itertools
import numpy as np
import pandas as pd

random.seed(100)
### params
n_transactions = 10000
phi = 0.5
decay = 1
beta = 0.5
uncertainity = 0.001
no_of_fake_feedback = 100
expinit = True #if True load 
#Ballot-Stuffing = 1
#Bad-mouthing = 2
#majority-descrimination = 3
#minority-descrimination = 4
#reentry = 5
#complementary = 6
#initial-window = 7
#On-off cannot be tested under the proposed method
#2, 3, 4
#get the first row users
scenario = 1



##setting up
#128 user, 102 consumers, 26 service providers
interactions2 = [(random.randrange(100, 128), random.randrange(110, 116), random.uniform(0, 1), random.uniform(0, 1), 'G') for i in range(n_transactions)]

##cleaning repetion
dt = pd.DataFrame(interactions2, columns=['Consumer', 'Producer', 'Consumerrating', 'Producerrating', 'TAG'])
dt = dt[dt['Consumer'] != dt['Producer']]
dt.reset_index(drop=True, inplace=True)
dt = dt.sort_values('Consumer', ignore_index=True)

##reomving same ids
uniqueid1list = dt.Consumer.unique().tolist()
print(uniqueid1list)
dn = pd.DataFrame()
indexlist = []
for i in uniqueid1list:
    for index,row in dt.iterrows():
        row = row.copy()
        if row['Producer'] == i: #and index not in indexlist
            dt.loc[index, 'Producer'] = row['Consumer']
            dt.loc[index, 'Consumer'] = row['Producer']

if expinit:
    datainitifilename = 'scenario_init'+str(scenario)+'_data.csv'
#     dt.to_csv(datainitifilename, index=False)
else:
    
    datainitifilename = 'scenario_init'+str(scenario)+'_data.csv'
    cereal_df2 = pd.read_csv(datainitifilename)
    
    datafinalfilename = 'scenario_final'+str(scenario)+'_data.csv'
    #attack scenario
    dt.head(1).Consumer.item()
    for i in range(no_of_fake_feedback):
        if scenario == 1:
            
            new_row = {'Consumer': dt.head(1).Consumer.item(), 'Producer':dt.head(1).Producer.item(), 'Consumerrating':1, 'Producerrating':random.uniform(0, 1), 'TAG':'F'}
            
        elif scenario == 2:
            new_row = {'Consumer': dt.head(1).Consumer.item(), 'Producer':dt.head(1).Producer.item(), 'Consumerrating':0.001, 'Producerrating':random.uniform(0, 1), 'TAG':'F'}
        elif scenario == 3:
            if (i > no_of_fake_feedback * 0.2) :
                new_row = {'Consumer': dt.head(1).Consumer.item(), 'Producer':dt.head(1).Producer.item(), 'Consumerrating':1, 'Producerrating':random.uniform(0, 1), 'TAG':'F'}
            else:
                new_row = {'Consumer': dt.head(1).Consumer.item(), 'Producer':dt.head(1).Producer.item(), 'Consumerrating':0.001, 'Producerrating':random.uniform(0, 1), 'TAG':'F'}
        elif scenario == 4:
            if (i > no_of_fake_feedback * 0.2) :
                new_row = {'Consumer': dt.head(1).Consumer.item(), 'Producer':dt.head(1).Producer.item(), 'Consumerrating':0.001, 'Producerrating':random.uniform(0, 1), 'TAG':'F'}
            else:
                new_row = {'Consumer': dt.head(1).Consumer.item(), 'Producer':dt.head(1).Producer.item(), 'Consumerrating':1, 'Producerrating':random.uniform(0, 1), 'TAG':'F'}
        elif scenario == 5:
            if (i == 1) :
                new_row = {'Consumer': dt.head(1).Consumer.item(), 'Producer':106, 'Consumerrating':random.uniform(0, 1), 'Producerrating':random.uniform(0, 1), 'TAG':'F'}
        elif scenario == 6:
            if (i > no_of_fake_feedback * 0.5) :
                new_row = {'Consumer': dt.head(1).Consumer.item(), 'Producer':dt.head(1).Producer.item(), 'Consumerrating':0.001, 'Producerrating':1, 'TAG':'F'}
            else:
                 new_row = {'Consumer': dt.head(1).Consumer.item(), 'Producer':dt.head(1).Producer.item(), 'Consumerrating':1, 'Producerrating':0.001, 'TAG':'F'}
    #     elif scenario == 7:
            ##TODO set neighbors/advisors to 02
        dt = dt.append(new_row, ignore_index=True)
        target_test_user = 115
        if (i <= int(no_of_fake_feedback/4)):
            new_row2 = {'Consumer': target_test_user, 'Producer':dt.head(1).Producer.item(), 'Consumerrating':random.uniform(0, 1), 'Producerrating':random.uniform(0, 1), 'TAG':'AG'}
            dt = dt.append(new_row2, ignore_index=True)
            new_row3 = {'Consumer': target_test_user-1, 'Producer':dt.head(1).Producer.item(), 'Consumerrating':random.uniform(0, 1), 'Producerrating':random.uniform(0, 1), 'TAG':'AG'}
            dt = dt.append(new_row3, ignore_index=True)
            new_row4 = {'Consumer': target_test_user-2, 'Producer':dt.head(1).Producer.item(), 'Consumerrating':random.uniform(0, 1), 'Producerrating':random.uniform(0, 1), 'TAG':'AG'}
            dt = dt.append(new_row4, ignore_index=True)
            new_row5 = {'Consumer': target_test_user-3, 'Producer':dt.head(1).Producer.item(), 'Consumerrating':random.uniform(0, 1), 'Producerrating':random.uniform(0, 1), 'TAG':'AG'}
            dt = dt.append(new_row5, ignore_index=True)
            new_row6 = {'Consumer': target_test_user-4, 'Producer':dt.head(1).Producer.item(), 'Consumerrating':random.uniform(0, 1), 'Producerrating':random.uniform(0, 1), 'TAG':'AG'}
            dt = dt.append(new_row6, ignore_index=True)
            new_row7 = {'Consumer': target_test_user-5, 'Producer':dt.head(1).Producer.item(), 'Consumerrating':random.uniform(0, 1), 'Producerrating':random.uniform(0, 1), 'TAG':'AG'}
            dt = dt.append(new_row7, ignore_index=True)
                
        dt.to_csv(datafinalfilename, index=False)

##seeing the data
user = 'Consumer'
if user == 'Consumer':
    vd = dt.groupby(['Consumer', 'Producer'])
for k, uid in vd:
    print(uid)

##func one
def get_uid(vd, phi, decay, user):
    newDF = pd.DataFrame()
        
    for k, uid in vd:
        itr_list = uid[user+'rating'].tolist()
#         print(itr_list)
        cum_rj = 0
        cum_sj = 0
        exp_val_n = len(itr_list)
        count = 0
        sj_list = []
        rj_list = []
        cum_sj_list = []
        cum_rj_list = []
        
#         for i in itr_list:
        print('=========================================================')
        for index, row in uid.iterrows():
            count += 1
            rj = ((1- row[user+'rating']) * phi) * (decay **(exp_val_n - count)) #disatisfaction
            sj = ((1+ row[user+'rating']) * phi) * (decay **(exp_val_n - count)) #satisfaction
            cum_rj += rj
            cum_sj += sj
            

#             print('rj ='+ str(rj)+', sj = '+str(sj))
            sj_list.append(sj)
            rj_list.append(rj)
            cum_sj_list.append(cum_sj)
            cum_rj_list.append(cum_rj)
            
            
        
#         print('vendor = '+ str(k)+', st ='+ str(rj)+', ds = '+str(sj))
        uid[user+'dis'] = rj_list  #disatisfaction list
        uid[user+'sat'] = sj_list #satisfaction list
        uid[user+'cum_dis'] = cum_rj_list #cummilative disatisfaction list
        uid[user+'cum_sat'] = cum_sj_list #cummilative satisfaction list
        

        print(uid)
        newDF = newDF.append(uid, ignore_index = True)
    return newDF

##setting decay and calling function one

df = get_uid(vd, phi, decay, user)

##getting ready to call again
user = 'Producer'
df.reset_index(drop=True, inplace=True)
# df
cd = df.groupby(['Consumer', 'Producer'])
df = get_uid(cd, phi, decay, user)

###reseting and grouping df
user = 'Consumer'
df.reset_index(drop=True, inplace=True)
df

cd = df.groupby(['Consumer'])

##  function two
def honesty(df, user='Consumer'):
    honDF = pd.DataFrame()
    for k, af in df:
        print(af)
        hon_li = []
        cum_cumsat = 0
        cum_cumdis = 0
        for index, row in af.iterrows():
            hon = 0
            cum_cumsat += row['Producer'+ 'cum_sat']
            cum_cumdis += row['Producer'+ 'cum_dis']
#             hon = cum_cumsat / (cum_cumsat + cum_cumdis)
            hon = 1 - (cum_cumdis / (cum_cumsat + cum_cumdis))
            print('hon')
            print(hon)
            hon_li.append(hon)

        af['honesty'] = hon_li
        print(af)
        honDF = honDF.append(af, ignore_index = True)
    return honDF

##calling honesty
hon_df = honesty(cd) #for adviser

#func three
def bayes(df, user='Consumer'):
    honDF = pd.DataFrame()
    df.reset_index(drop=True, inplace=True)
    cd = df.groupby(['Consumer'])
    for k, af in cd:
        print(af)
        hon_li = []
        cum_cumsat = 0
        cum_cumdis = 0
        for index, row in af.iterrows():
            expectedtrust = 0
            initr = 0
            inits = 0
            cum_cumsat += row['Consumer'+ 'cum_sat']
            cum_cumdis += row['Consumer'+ 'cum_dis']
#             hon = cum_cumsat / (cum_cumsat + cum_cumdis)
            expectedtrust =  (initr + cum_cumsat) / (initr + inits + cum_cumsat + cum_cumdis)
            print('expectedtrust')
            print(expectedtrust)
            hon_li.append(expectedtrust)

        af['bayesT'] = hon_li
        print(af)
        honDF = honDF.append(af, ignore_index = True)
    return honDF

bdf = bayes(hon_df)

#range 0-1
def get_belief_implicit(cd, epsilon, user):
#     tricky here, col.sum would result different than len(col)

    newdDF = pd.DataFrame()
    for k, af in cd:
        print(af)
        

        dbis = []
        bellis = []
        unlis = []
        
        
        
        for index, row in af.iterrows():
            cum_dis = 0
            cum_sat = 0
            total_sat_dit = 0
            den = 0
            
            cum_dis = row[user+'cum_dis'] 
            cum_sat = (row[user+'cum_sat'])


            print('cum_dis')
            print(cum_dis)
            print('cum_sat')
            print(cum_sat)
            print('total')
            total_sat_dit = cum_dis+cum_sat
            den = total_sat_dit + epsilon 
            print(total_sat_dit)
            belief = cum_sat /(den)
            disbelief = cum_dis /(den)
            uncertainity = epsilon / (den)
            
            dbis.append(disbelief)
            bellis.append(belief)
            unlis.append(uncertainity)
 

        af[user+'bel'] = bellis
        af[user+'disbel'] = dbis
        af[user+'unc'] = unlis

        print(af)
        newdDF = newdDF.append(af, ignore_index = True)


    return newdDF

user = 'Consumer'
bdf.reset_index(drop=True, inplace=True)

cd = bdf.groupby(['Consumer'])


df_dbu =get_belief_implicit(cd,uncertainity, user)

def distancematrix(df):
    uniqueid1list = df.Consumer.unique().tolist()
    comb = list(itertools.combinations(uniqueid1list,2))
    distance_matrix = [[0 for i in range(len(uniqueid1list))] for j in range(len(uniqueid1list))]
    sim_matrix = [[0 for i in range(len(uniqueid1list))] for j in range(len(uniqueid1list))]
    print(distance_matrix)
    print(comb)
    print(uniqueid1list)
    
    idxtoid = {}
    idtoidx = {}
    count = 0
    for i in uniqueid1list:
        idxtoid[count] = i
        idtoidx[i] = count #mostly used
        count += 1

    cd = df.groupby(['Consumer', 'Producer'])

    
    distance_li = []
    normalized_dist = []
    
    ##initializing vendor list
    vendors = {}
    cm_vendors = {}
    
    comv_advisors = {}
    for i in uniqueid1list:
        v = []
        for x, af in cd:
            if(x[0]==i):
#                 print(x[1])
                v.append(x[1])
        vendors[i] = v    
    
    

    for j in uniqueid1list:
        com_ad = []
        for k in uniqueid1list:
            if( j!= k):
                print('===================pairs================')
                print('requestor '+str(j)+' vendors ='+str(vendors[j]))
                print('advisor '+str(k)+' vendors ='+str(vendors[k]))
                comm_vendors =  [v for v, u in zip(vendors[j], vendors[k]) if u == v]
                
                print('common vendors ='+str(comm_vendors))
                cum_dist = 0
                meand = 0
                
                print('searchin for vendor entries===')
                for cv in comm_vendors:
                    
                    nonsqrt = 0
                    dist = 0
                    for x, af in cd:
                        if(x[0]==j and x[1]==cv):
                            print('set i entry')
                            a_bel = 0
                            a_disbel = 0
                            a_unc = 0
                            print(x)
#                             print(af.Consumerbel.tail(1))
#                             print(af.Consumerdisbel.tail(1))
#                             print(af.Consumerunc.tail(1))
                            a_bel = af.Consumerbel.tail(1).item()
                            a_disbel = af.Consumerdisbel.tail(1).item()
                            a_unc = af.Consumerunc.tail(1).item()
                        if(x[0]==k and x[1]==cv):
                            print('set j entry')
                            b_bel = 0
                            b_disbel = 0
                            b_unc = 0
                            print(x)
#                             print(af.Consumerbel.tail(1))
#                             print(af.Consumerdisbel.tail(1))
#                             print(af.Consumerunc.tail(1))
                            b_bel = af.Consumerbel.tail(1).item()
                            b_disbel = af.Consumerdisbel.tail(1).item()
                            b_unc = af.Consumerunc.tail(1).item()
            
                    nonsqrt=((a_bel - b_bel)**2) + ((a_disbel - b_disbel)**2) + ((a_unc - b_unc)**2)
                    dist = nonsqrt** (1/2)
                    dist = dist/2
                    cum_dist += dist
                print('searchin for vendor entries===end')
                if len(comm_vendors) > 0:
                    meand = cum_dist/len(comm_vendors)
                    distance_matrix[idtoidx[j]][idtoidx[k]] = meand
                    sim_matrix[idtoidx[j]][idtoidx[k]] = 1 - meand #Note that this would give 0 if no vendor since it initialize with 0
                    cm_vendors[(j,k)] = comm_vendors
                    com_ad.append(k)
                
                print('======mean distance beteween' +str(j) +' and '+str(k)+' = '+str(meand)+'======')
                print('======sim' +str(j) +' and '+str(k)+' = '+str(1 - meand)+'======')
        comv_advisors[j] = com_ad               
        
    return distance_matrix, sim_matrix, idxtoid, idtoidx, cm_vendors, comv_advisors


##calling distance function
d, sim, idx_id, id_idx, commonv, comv_advisors =distancematrix(df_dbu)


# rep function
def reputation3(df, sim, id_idx, idx_id, commonv, comv_advisors, user='Consumer', alpha=0.2):
    uniqueid1list = df.Consumer.unique().tolist()
    uniqueproducersl = df.Producer.unique().tolist()
    rep_matrix = [[0 for i in range(len(uniqueid1list))] for j in range(len(uniqueproducersl))]
    print(commonv)
    
    mf = df.groupby(['Consumer', 'Producer']) 
    pf = df.groupby(['Producer'])

    
    vidx_vid = {}
    vid_vidx = {}
    count = 0
    for i in uniqueproducersl:
        vidx_vid[count] = i
        vid_vidx[i] = count #mostly used
        count += 1
    print(vidx_vid)
    print(vid_vidx)
    
    v_neigbors = {}
    for y, gf in pf:
        print(gf.Consumer.unique())
        v_neigbors[y] = gf.Consumer.unique().tolist()
    

    print('len(v_neigbors)'+str(len(v_neigbors)))
    print('len(uniqueproducersl'+str(len(uniqueproducersl)))

    vra_rep = {} #(vendor requestor advisor) = reputaion
    for vendor in v_neigbors:
#         print(key) 
        for requestor in uniqueid1list:
#             print(v_neigbors[vendor])
            hon = 0
            rep = 0
            hon_count = 0 #this is m in equation
            rep_count = 0 #this in n in equation

            for advisor in v_neigbors[vendor]:

                if((advisor,requestor) in commonv):
                    ab_sim = sim[id_idx[requestor]][id_idx[advisor]]
                    cum_result = 0
                    print('...commvl'+str((advisor,requestor)))
                    for x, af in mf:
                        if(x[0]==advisor and x[1]==vendor):
                            av_bel = af.Consumerbel.tail(1).item()
                            rep += (ab_sim * av_bel)
                            rep_count += 1

                else:
                    print('no common pairs '+ str((advisor,requestor)))
                    print('so we want '+ str(vendor)+' honesty with '+str(advisor))
                
                    for y, jf in mf: #in this loop following condition will occur only once
                        if(y[0]==advisor and y[1]==vendor): 
                            av_bel = jf.Consumerbel.tail(1).item()
                            va_hon = jf.honesty.tail(1).item()
                            hon += (av_bel * va_hon)
                            hon_count += 1
            reputation = 0
            if rep_count > 0:
                reputation = (alpha * rep)/rep_count
            
            if hon_count > 0:
                reputation += ((1 - alpha) * hon)/hon_count
            
            vra_rep[(vendor, requestor)] = reputation
    return vra_rep


##calling repfuction
vendor_requestor_rep = reputation3(df_dbu, sim, id_idx, idx_id, commonv, comv_advisors)
vendor_requestor_rep

##initial trust
##TODO setup trust_propensity for all users
def init_trust(df, rep, beta=0.5):
    requestor_li = df.Consumer.unique().tolist()
    vendor_lis = df.Producer.unique().tolist()
    rv_initT = {}
    for vendor in vendor_lis:
        for requestor in requestor_li:
            trust_propensity = random.uniform(0, 1)
            r = 0
            if (vendor, requestor) in rep:
                r = rep[(vendor, requestor)]
            initT = (beta * trust_propensity ) + ((1-beta) * r)
            rv_initT[(requestor,vendor)] = initT
    return rv_initT

##calling initrust
intTrustm = init_trust(df_dbu, vendor_requestor_rep, beta)


def trust_T(df,initT, beta=0.5):
    mf = df.groupby(['Consumer', 'Producer'])
    tDtDF = pd.DataFrame()
    for k, af in mf:
        print(k)
        print(af)
        trust_li = []
        trust_dash_li = []
        sum_test = []
        t = 0
        trust_propensity = random.uniform(0, 1)
        for index, row in af.iterrows():
            trust = 0
            trust_dash = 0
            sum_t = 0
#             t = row['init_T'+str(user)]
            if (k[1], k[0]) in initT:
                t = initT[(k[1], k[0])]
            b = row['Consumerbel']
            d = row['Consumerdisbel']
            u = row['Consumerunc']
            trust = b + (t * u)
            trust_dash = d + ((1 - t) * u) 
            sum_t = trust + trust_dash
            print('sum_t')
            print(sum_t)
            trust_li.append(trust)
            trust_dash_li.append(trust_dash)
            sum_test.append(sum_t)

        af['ConsumerT'] = trust_li
        af['ConsumerT_dash'] = trust_dash_li
        af['Consumersum_tdt'] = sum_test
        print(af)
        tDtDF = tDtDF.append(af, ignore_index = True)   
    return tDtDF

##final trust
finDF = trust_T(df_dbu, intTrustm)

##saving file
if expinit:
    filename = 'scenario_init'+str(scenario)+'_trust.csv'
else:
    
    filename = 'scenario_final'+str(scenario)+'_trust.csv'

finDF.to_csv(filename, index=False)

[100, 101, 102, 103, 104, 105, 106, 107, 108, 109, 110, 111, 112, 113, 114, 115, 116, 117, 118, 119, 120, 121, 122, 123, 124, 125, 126, 127]
     Consumer  Producer  Consumerrating  Producerrating TAG
1         110       100        0.101087        0.390893   G
4         110       100        0.695087        0.002225   G
7         110       100        0.816721        0.807565   G
10        110       100        0.891100        0.583221   G
14        110       100        0.551434        0.877552   G
..        ...       ...             ...             ...  ..
357       110       100        0.745786        0.469720   G
358       110       100        0.334866        0.989842   G
361       110       100        0.041945        0.194342   G
380       110       100        0.917678        0.826869   G
381       110       100        0.372364        0.352849   G

[66 rows x 5 columns]
     Consumer  Producer  Consumerrating  Producerrating TAG
390       110       101        0.266634        0.058039 

[122 rows x 5 columns]
     Consumer  Producer  Consumerrating  Producerrating TAG
12        115       100        0.280583        0.537014   G
13        115       100        0.570017        0.692928   G
42        115       100        0.163301        0.302413   G
50        115       100        0.675681        0.274512   G
55        115       100        0.462861        0.957079   G
..        ...       ...             ...             ...  ..
359       115       100        0.629388        0.106992   G
366       115       100        0.870078        0.714176   G
367       115       100        0.599709        0.018377   G
376       115       100        0.154758        0.079657   G
386       115       100        0.228644        0.285377   G

[66 rows x 5 columns]
     Consumer  Producer  Consumerrating  Producerrating TAG
389       115       101        0.174993        0.515671   G
392       115       101        0.039402        0.633673   G
401       115       101        0.381922        0.95858

7185       120       112        0.260779        0.775040   G
      Consumer  Producer  Consumerrating  Producerrating TAG
6870       120       113        0.632956        0.136063   G
6875       120       113        0.773734        0.913504   G
6879       120       113        0.196049        0.229345   G
6882       120       113        0.267417        0.177138   G
6883       120       113        0.506309        0.705251   G
...        ...       ...             ...             ...  ..
7166       120       113        0.203160        0.132648   G
7168       120       113        0.351180        0.926024   G
7173       120       113        0.642821        0.248073   G
7174       120       113        0.829638        0.905226   G
7187       120       113        0.963392        0.196429   G

[64 rows x 5 columns]
      Consumer  Producer  Consumerrating  Producerrating TAG
6867       120       114        0.335148        0.873539   G
6869       120       114        0.011447        0.512712   G
6

[69 rows x 5 columns]
      Consumer  Producer  Consumerrating  Producerrating TAG
9279       127       114        0.565153        0.455019   G
9281       127       114        0.579466        0.503876   G
9296       127       114        0.714227        0.796873   G
9308       127       114        0.987709        0.198464   G
9331       127       114        0.717548        0.330628   G
...        ...       ...             ...             ...  ..
9643       127       114        0.128737        0.643837   G
9644       127       114        0.956532        0.846451   G
9655       127       114        0.958466        0.474368   G
9656       127       114        0.143329        0.833216   G
9659       127       114        0.712565        0.798430   G

[63 rows x 5 columns]
      Consumer  Producer  Consumerrating  Producerrating TAG
9280       127       115        0.405793        0.147924   G
9284       127       115        0.793830        0.057280   G
9285       127       115        0.287671

1107     0.771411        13.097408        38.902592  
      Consumer  Producer  Consumerrating  Producerrating TAG  Consumerdis  \
1117       111       103        0.077173        0.733372   G     0.461414   
1124       111       103        0.978911        0.062477   G     0.010544   
1125       111       103        0.331807        0.018609   G     0.334096   
1133       111       103        0.474808        0.384102   G     0.262596   
1139       111       103        0.392872        0.996729   G     0.303564   
1151       111       103        0.804186        0.401556   G     0.097907   
1152       111       103        0.005645        0.395516   G     0.497177   
1157       111       103        0.743142        0.085736   G     0.128429   
1164       111       103        0.873784        0.861492   G     0.063108   
1177       111       103        0.317694        0.252052   G     0.341153   
1179       111       103        0.099275        0.870108   G     0.450362   
1193       111       1

...

[48 rows x 21 columns]
(125, 112)
      Consumer  Producer  Consumerrating  Producerrating TAG  Consumerdis  \
8713       125       112        0.142091        0.323616   G     0.428954   
8714       125       112        0.341727        0.144132   G     0.329136   
8715       125       112        0.320729        0.964167   G     0.339635   
8716       125       112        0.962645        0.680351   G     0.018678   
8717       125       112        0.630740        0.764567   G     0.184630   
...        ...       ...             ...             ...  ..          ...   
8771       125       112        0.014582        0.542939   G     0.492709   
8772       125       112        0.829681        0.621339   G     0.085160   
8773       125       112        0.028734        0.421367   G     0.485633   
8774       125       112        0.172670        0.904773   G     0.413665   
8775       125       112        0.308548        0.400541   G     0.345726   

      Consumersat  Consumercum_dis  Consu

[58 rows x 21 columns]
(126, 110)
      Consumer  Producer  Consumerrating  Producerrating TAG  Consumerdis  \
8947       126       110        0.391512        0.464099   G     0.304244   
8948       126       110        0.548674        0.528440   G     0.225663   
8949       126       110        0.575285        0.680641   G     0.212358   
8950       126       110        0.743796        0.642225   G     0.128102   
8951       126       110        0.656246        0.163870   G     0.171877   
8952       126       110        0.483723        0.491907   G     0.258139   
8953       126       110        0.670364        0.569489   G     0.164818   
8954       126       110        0.801904        0.084701   G     0.099048   
8955       126       110        0.471064        0.002157   G     0.264468   
8956       126       110        0.251601        0.273212   G     0.374200   
8957       126       110        0.341707        0.798987   G     0.329147   
8958       126       110        0.716476  

[53 rows x 21 columns]
(126, 114)
      Consumer  Producer  Consumerrating  Producerrating TAG  Consumerdis  \
9171       126       114        0.597441        0.857724   G     0.201279   
9172       126       114        0.172792        0.661748   G     0.413604   
9173       126       114        0.150518        0.112330   G     0.424741   
9174       126       114        0.294518        0.402655   G     0.352741   
9175       126       114        0.515967        0.907241   G     0.242017   
9176       126       114        0.327509        0.188203   G     0.336246   
9177       126       114        0.903036        0.433155   G     0.048482   
9178       126       114        0.654943        0.717795   G     0.172528   
9179       126       114        0.939461        0.243456   G     0.030269   
9180       126       114        0.510145        0.130581   G     0.244927   
9181       126       114        0.532133        0.325868   G     0.233934   
9182       126       114        0.634322  

[62 rows x 21 columns]
(127, 112)
      Consumer  Producer  Consumerrating  Producerrating TAG  Consumerdis  \
9411       127       112        0.108479        0.724738   G     0.445760   
9412       127       112        0.168978        0.809234   G     0.415511   
9413       127       112        0.771270        0.164978   G     0.114365   
9414       127       112        0.793026        0.285979   G     0.103487   
9415       127       112        0.254831        0.539668   G     0.372585   
...        ...       ...             ...             ...  ..          ...   
9468       127       112        0.248622        0.337386   G     0.375689   
9469       127       112        0.751263        0.344375   G     0.124369   
9470       127       112        0.987183        0.899861   G     0.006408   
9471       127       112        0.578178        0.095988   G     0.210911   
9472       127       112        0.359742        0.100044   G     0.320129   

      Consumersat  Consumercum_dis  Consu

sum_t
1.0
sum_t
1.0000000000000002
sum_t
1.0
sum_t
1.0
sum_t
1.0
sum_t
1.0
sum_t
1.0
sum_t
1.0
sum_t
1.0
sum_t
1.0
sum_t
1.0
sum_t
1.0
sum_t
1.0
sum_t
1.0
sum_t
1.0
sum_t
0.9999999999999999
sum_t
1.0
sum_t
1.0
sum_t
1.0
      Consumer  Producer  Consumerrating  Producerrating TAG  Consumerdis  \
9605       127       115        0.405793        0.147924   G     0.297103   
9606       127       115        0.793830        0.057280   G     0.103085   
9607       127       115        0.287671        0.682530   G     0.356165   
9608       127       115        0.652532        0.129840   G     0.173734   
9609       127       115        0.941008        0.771837   G     0.029496   
9610       127       115        0.455752        0.612176   G     0.272124   
9611       127       115        0.671175        0.493666   G     0.164412   
9612       127       115        0.600849        0.653497   G     0.199575   
9613       127       115        0.714744        0.766958   G     0.142628   
9614      